# Лабораторная работа №3
## по предмету "Системы искусственного интеллекта"

Целью работы является изучение методов регуляризации.


### Задание 1

Выгрузите данные из датасета. Изучите колонки, проверьте наличие пропусков. Постройте матрицу корреляции между признаками и целевой переменной. Сделайте выводы, что показывает эта матрица.

In [128]:
import pandas as pd

df = pd.read_csv('AISP2.csv')

df.head()

brand processor_brand processor_name processor_gnrtn ram_gb ram_type  \
0    ASUS           Intel        Core i3            10th   4 GB     DDR4   
1  Lenovo           Intel        Core i3            10th   4 GB     DDR4   
2  Lenovo           Intel        Core i3            10th   4 GB     DDR4   
3    ASUS           Intel        Core i5            10th   8 GB     DDR4   
4    ASUS           Intel   Celeron Dual   Not Available   4 GB     DDR4   

      ssd      hdd       os  os_bit graphic_card_gb  weight     warranty  \
0    0 GB  1024 GB  Windows  64-bit            0 GB  Casual  No warranty   
1    0 GB  1024 GB  Windows  64-bit            0 GB  Casual  No warranty   
2    0 GB  1024 GB  Windows  64-bit            0 GB  Casual  No warranty   
3  512 GB     0 GB  Windows  32-bit            2 GB  Casual  No warranty   
4    0 GB   512 GB  Windows  64-bit            0 GB  Casual  No warranty   

  Touchscreen msoffice  Price   rating  Number of Ratings  Number of Reviews  
0          No       No  34649  2 stars                  3                  0  
1          No       No  38999  3 stars                 65                  5  
2          No       No  39999  3 stars                  8                  1  
3          No       No  69990  3 stars                  0                  0  
4          No       No  26990  3 stars                  0                  0

In [118]:
display(df.isnull().sum())
display(df.isna().sum())

brand                0
processor_brand      0
processor_name       0
processor_gnrtn      0
ram_gb               0
ram_type             0
ssd                  0
hdd                  0
os                   0
os_bit               0
graphic_card_gb      0
weight               0
warranty             0
Touchscreen          0
msoffice             0
Price                0
rating               0
Number of Ratings    0
Number of Reviews    0
dtype: int64

brand                0
processor_brand      0
processor_name       0
processor_gnrtn      0
ram_gb               0
ram_type             0
ssd                  0
hdd                  0
os                   0
os_bit               0
graphic_card_gb      0
weight               0
warranty             0
Touchscreen          0
msoffice             0
Price                0
rating               0
Number of Ratings    0
Number of Reviews    0
dtype: int64

In [119]:
df['ram_gb'] = df['ram_gb'].str.replace(' GB', '').astype(float)
df['ssd'] = df['ssd'].str.replace(' GB', '').astype(float)
df['hdd'] = df['hdd'].str.replace(' GB', '').astype(float)
df['graphic_card_gb'] = df['graphic_card_gb'].str.replace(' GB', '').astype(float)
df['rating'] = df['rating'].str.replace(' stars', '').str.replace(' star', '').astype(float)

df = pd.get_dummies(df, 
    columns=['brand', 'processor_brand', 'processor_name', 'ram_type', 
             'os', 'os_bit', 'Touchscreen', 'msoffice', 'warranty', 'processor_gnrtn', 'weight'])

df.corr(numeric_only=True)['Price'].sort_values(ascending=False)

Price                            1.000000
ssd                              0.628272
ram_gb                           0.518323
graphic_card_gb                  0.459986
processor_name_Core i7           0.377777
processor_name_Core i9           0.359096
brand_APPLE                      0.312112
os_Mac                           0.312112
processor_name_M1                0.274581
processor_brand_M1               0.274581
processor_name_Ryzen 9           0.253506
weight_Casual                    0.247878
processor_gnrtn_12th             0.219060
Touchscreen_Yes                  0.189126
ram_type_LPDDR3                  0.181314
ram_type_LPDDR4X                 0.173809
ram_type_DDR5                    0.168689
processor_gnrtn_10th             0.164034
os_DOS                           0.140780
brand_MSI                        0.123952
msoffice_No                      0.105752
warranty_3 years                 0.080610
processor_name_Ryzen 7           0.061872
ram_type_DDR3                    0

In [120]:
df.dtypes


ram_gb                           float64
ssd                              float64
hdd                              float64
graphic_card_gb                  float64
Price                              int64
rating                           float64
Number of Ratings                  int64
Number of Reviews                  int64
brand_APPLE                         bool
brand_ASUS                          bool
brand_Avita                         bool
brand_DELL                          bool
brand_HP                            bool
brand_Lenovo                        bool
brand_MSI                           bool
brand_acer                          bool
processor_brand_AMD                 bool
processor_brand_Intel               bool
processor_brand_M1                  bool
processor_name_Celeron Dual         bool
processor_name_Core i3              bool
processor_name_Core i5              bool
processor_name_Core i7              bool
processor_name_Core i9              bool
processor_name_M

In [121]:
from sklearn.model_selection import train_test_split

y = df['Price']

X = df.drop('Price', axis=1)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

### Задание 2

Реализуйте алгоритм линеной регрессии  без использования регуляризации.

In [122]:
from sklearn.linear_model import LinearRegression

model = LinearRegression()
model.fit(X_train, y_train)

LinearRegression()

In [123]:
import numpy as np

from sklearn.metrics import mean_squared_error, r2_score

y_pred = model.predict(X_test)

mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f'MSE: {mse:.2f}')
print(f"RMSE: {np.sqrt(mse):.2f}") # рублей
print(f'R²: {r2:.4f}')

MSE: 638671150.10
RMSE: 25271.94
R²: 0.6723


### Задание 3

Реализуйте алгоритм линейной регрессии с L1-регуляризацией.

In [124]:
from sklearn.linear_model import Lasso
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

lasso = make_pipeline(StandardScaler(), Lasso(alpha=100, random_state=42))
lasso.fit(X_train, y_train)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('lasso', Lasso(alpha=100, random_state=42))])

In [125]:
y_pred = lasso.predict(X_test)
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f"MSE: {mse:.2f}")
print(f"RMSE: {np.sqrt(mse):.2f}")
print(f"R²: {r2:.4f}")

MSE: 608702817.47
RMSE: 24671.90
R²: 0.6877


### Задание 4

Реализуйте алгоритм линейной регрессии с L2-регуляризацией.

In [126]:
from sklearn.linear_model import Ridge

ridge = make_pipeline(StandardScaler(), Ridge(alpha=100, random_state=42))
ridge.fit(X_train, y_train)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('ridge', Ridge(alpha=100, random_state=42))])

In [127]:
y_pred = ridge.predict(X_test)

mse = mean_squared_error(y_test, y_pred)
rmse = np.sqrt(mse)
r2 = r2_score(y_test, y_pred)

print(f"MSE: {mse:.2f}")
print(f"RMSE: {rmse:.2f}")
print(f"R²: {r2:.4f}")

MSE: 576791993.95
RMSE: 24016.49
R²: 0.7040


### Задание 5

Сделайте выводы о результатах обучения.